- Each type of **Optic** comes with a set of compatible **actions**.

Lenses have the following concrete gaurantees.

* A Lens focuses (i.e selects) a single piece of data within a larger structure.
* A Lens must **never fail** to **get** or **modify** that focus.

These constraints unlock a few **actions** we can perform on lenses.

* We can use a lens to **view** the **focus** within a structure.
* We can use a lens to **set** the **focus** within a structure.
* We can use a lens to **modify** the **focus** within a structure.

In [14]:
{-# LANGUAGE TemplateHaskell #-}
{-# LANGUAGE FlexibleInstances #-}
{-# LANGUAGE FlexibleContexts #-}
{-# LANGUAGE RankNTypes #-}
{-# LANGUAGE ScopedTypeVariables #-}
{-# LANGUAGE TypeApplications #-}
{-# LANGUAGE TypeFamilies #-}
{-# LANGUAGE InstanceSigs #-}

import Control.Lens
import Numeric.Lens
import Data.Bits.Lens
import Data.Data.Lens

import Control.Applicative
import Data.Char as C
import qualified Data.Map as M
import qualified Data.Set as S
import qualified Data.Text as T
import qualified Data.List as L

view (_2 . _1) (42, ("hello", False))

-- view is the action
-- (_2 . _1) is the path
-- (42, ("hello", False)) is the structure
-- "hello" is the focus

"hello"

## Exercises - Optic Anatomy

In [16]:
view (_1 . _2) ((1, 2), 3)

-- view is the action
-- (_1 . _2) is the path. Focus on the 1st member of tuple and then the 2nd member of 1st member
-- ((1, 2), 3) is the structure
-- 2 is the focus

set (_2 . _Left) "new" (False, Left "old")

-- set is the action
-- (_2 . _Left) is the path
-- (False, Left "Old") is the structure
-- "old" is the focus

over (taking 2 worded . traversed) C.toUpper "testing one two three"

-- over is the action
-- (taking 2 worded . traversed) is the path
-- "testing one two three"
-- "testing one" is the focus

foldOf (both . each) (["super", "cali"],["fragilistic", "expialidocious"])

-- foldOf is the action
-- (both . each) is the path
-- The rest is the structure

2

(False,Left "new")

"TESTING ONE two three"

"supercalifragilisticexpialidocious"

## Lens Actions

### Viewing through lenses

In [25]:
:t _1

:k Lens'
:k Lens

-- _1 :: Lens' (a, b) a
--             (a, b) --> Type of structure
--                    a --> Focus within it

:t _2

:t view

-- A lens on it's own isn't enough. We need an action to perform on it.

-- view :: Lens' s a -> s -> a
--         Get the path's focus from within the structure

view _1 ('a', 'b')

view _2 ('a', 'b')

_1 :: forall s t a b (f :: * -> *). (Field1 s t a b, Functor f) => (a -> f b) -> s -> f t

Lens' :: * -> * -> *

Lens :: * -> * -> * -> * -> *

_2 :: forall s t a b (f :: * -> *). (Field2 s t a b, Functor f) => (a -> f b) -> s -> f t

view :: forall s (m :: * -> *) a. MonadReader s m => Getting a s a -> m a

'a'

'b'

### Setting through a lens

In [28]:
-- set :: Lens' s a -> a -> s -> s
--        Set a new value at the path’s focus, leaving the rest of the structure unaltered.

-- over :: Lens' s a -> (a -> a) -> s -> s
--         Modify the focus of a path by running a function over it, altering it in-place and leaving the
--         rest of the structure unaltered.

:t set
:t over

set _1 'x' ('a', 'b')

over _1 (*100) (1, 2)

set :: forall s t a b. ASetter s t a b -> b -> s -> t

over :: forall s t a b. ASetter s t a b -> (a -> b) -> s -> t

('x','b')

(100,2)

## Exercises - Lens Actions

In [30]:
-- 1. Find structure & focus in the following lens

-- Lens' (Bool, (Int, String)) Int

-- (Bool, (Int, String)) is the structure
-- Focus is Int, the 1st member of the 2nd member of the complete structure

-- 2. Write the type signature of a Lens with the structure (Char, Int) and the focus Char

-- Lens' (Char, Int) Char

-- 3. Name three actions we can use on a Lens

-- set
-- view
-- over

-- 4

view _3 ('a', 'b', 'c')

over _2 (*10) (False, 2)

'c'

(False,20)

## Lenses and records

* Lenses subsume the accessor pattern in other languages.

In [47]:
-- Just changed the names from the example in the book
data Name = 
    Name { _name :: String
         , _age  :: Int
         } deriving (Show)
         
-- lens :: (s -> a) -> (s -> b -> t) -> Lens s t a b
-- lens :: (s -> a) -> (s -> a -> s) -> Lens' s a

:t lens
:k Lens
:k Lens'

-- Whenever you see 's' in a Lens thing 'structure' and when you see 'a', think 'focus'.

-- getAge :: s -> a
getAge :: Name -> Int
getAge = _age

-- setAge :: s -> a -> s
setAge :: Name -> Int -> Name
setAge name newAge = name { _age = newAge }

numAge :: Lens' Name Int
numAge = lens getAge setAge

lens :: forall (f :: * -> *) s a b t. Functor f => (s -> a) -> (s -> b -> t) -> (a -> f b) -> s -> f t

Lens :: * -> * -> * -> * -> *

Lens' :: * -> * -> *

## Exercises - Records Part One

In [62]:
-- 1. The structure and focus of a lens are typically represented by which letters in type signature
-- s and a respectively

-- 2. Which two components are required to create a lens
-- getter and setter

-- Implement the following Lens

-- name :: Lens' Name String

getName :: Name -> String
getName = _name

setName :: Name -> String -> Name
setName name newName = name { _name = newName }

name :: Lens' Name String
name = lens getName setName

myName :: Name
myName = Name { _name = "Sanchayan Maity"
              , _age  = 31 } 
              
-- Getting, setting & modifying with a field lens

-- For Age field
view numAge myName
set numAge 32 myName
over numAge (+3) myName
set numAge (view numAge myName + 3) myName

-- For Name field
view name myName
set name "Foo" myName
over name ("Boo " ++) myName

31

Name {_name = "Sanchayan Maity", _age = 32}

Name {_name = "Sanchayan Maity", _age = 34}

Name {_name = "Sanchayan Maity", _age = 34}

"Sanchayan Maity"

Name {_name = "Foo", _age = 31}

Name {_name = "Boo Sanchayan Maity", _age = 31}

## Automatically generating field names

In [67]:
data Ship = 
    Ship { _name :: String
         , _numCrew :: Int 
         } deriving (Show)

makeLenses ''Ship

:t name
:t numCrew
:t getNumCrew

name :: forall (f :: * -> *). Functor f => (String -> f String) -> Ship -> f Ship

numCrew :: forall (f :: * -> *). Functor f => (Int -> f Int) -> Ship -> f Ship

getNumCrew :: Ship -> Int

## Exercises - Records Part Two

In [72]:
-- data Inventory = 
--    Inventory { _wand :: Wand
--              , _book :: Book
--              , _potions :: [Potion] }

-- makeLenses ''Inventory

-- Lenses generated would be

-- wand
-- book
-- potions
-- getWand
-- getBook
-- getPotions
-- setWand
-- setBook
-- setPotions

-- gazork :: Functor f => (Spuzz -> f Spuzz) -> Chumble -> f Chumble
-- gazork :: Lens' Chumble Spuzz

data Pet = Pet 
    { _petName :: String
    , _petType :: String
    }
    
makeLenses ''Pet

getPetName :: Pet -> String
getPetName = view petName

### Lens is an optic which **always** accesses **exactly** one focus

### Is it a Lens?

* second :: Lens' (a, b, c) b

* inMaybe :: Lens' (Maybe a) a

* left :: Lens' (Either a b) a

* listThird :: Lens' [a] a

* Can you write a lens which focuses the second element of a tuple if the Bool in the first slot is True and focuses the third element if it’s False ? conditional :: Lens' (Bool, a, a) a

* Consider the below data type. Is it possible to have a lens msg :: Lens' Err String

In [75]:
data Err = 
    ReallyBadError { _msg :: String }
  | ExitCode { _code :: Int }


## Lens Laws

1. You get back what you set
2. Setting back what you got doesn't do anything
3. Setting twice is the same as setting once

## Virtual Fields

In [82]:
data Temperature = 
    Temperature { _location :: String
                , _celsius  :: Float
                } deriving (Show)
                
makeLenses ''Temperature

:t celsius

let temp = Temperature "Bangalore" 7.0

view celsius temp
set celsius 13.5 temp
over celsius (+10) temp

celsiusToFahrenheit :: Float -> Float
celsiusToFahrenheit c = (c * (9/5)) + 32

fahrenheitToCelsius :: Float -> Float
fahrenheitToCelsius f = (f - 32) * (5/9)

fahrenheit :: Lens' Temperature Float
fahrenheit = lens getter setter
    where
        getter = celsiusToFahrenheit . view celsius
        setter temp f = set celsius (fahrenheitToCelsius f) temp
        
view fahrenheit temp
set fahrenheit 56.3 temp
over fahrenheit (+18) temp

celsius :: forall (f :: * -> *). Functor f => (Float -> f Float) -> Temperature -> f Temperature

7.0

Temperature {_location = "Bangalore", _celsius = 13.5}

Temperature {_location = "Bangalore", _celsius = 17.0}

44.6

Temperature {_location = "Bangalore", _celsius = 13.5}

Temperature {_location = "Bangalore", _celsius = 17.0}

Note: TODO: The exercises on laws & virtual fields